**Import các thư viện**

In [1]:

from utils import helper, textprocessing
import os
import shelve
import pickle
from collections import Counter
import math
import json
import csv

**Đọc dữ liệu**

In [2]:
careerlink_path = os.path.join(os.getcwd(), 'db', 'careerlink.json')
careerbuilder_path = os.path.join(os.getcwd(), 'db', 'careerbuilder.json')

with open(careerlink_path, 'rb') as file:
    careerlink_data = json.load(file)

with open(careerbuilder_path, 'rb') as file:
    careerbuilder_data = json.load(file)

job_data = careerlink_data + careerbuilder_data

**Tạo corpus với url và token**

In [4]:
def get_corpus(dataset, stopwords_set):
    for url, text in dataset:
        if text != '':
            tokens = textprocessing.preprocess_text(text, stopwords_set)
             # In giá trị của tokens
            print(f'Tokens for URL {url}: {tokens}')
           
            yield url, Counter(tokens)

In [13]:
def get_corpus2(dataset, stopwords_set):
    for url, text ,industry in dataset:
        if text != '':
            tokens = textprocessing.preprocess_text(text, stopwords_set)
            #  # In giá trị của tokens
            # print(f'Tokens for URL {url}: {tokens}')
           
            yield url, Counter(tokens), industry

**Thu thập 2 trường url và title**

In [5]:
def crawl(jobs_data):
    for job in jobs_data:
        url = job['url']
        text = job['job_title']
        
        yield url,text

In [6]:
def get_corpora(stopwords_set, job_data):
    dataset = crawl(job_data)

    yield from get_corpus(dataset, stopwords_set)
   

**Tạo corpora**

In [15]:
stopwords_file = os.path.join(os.getcwd(), 'vietnamese-stopwords-dash.txt')
with open(stopwords_file, mode='r', encoding='utf-8') as f:
    stopwords_set = set(f.read().split())
    
corpora = get_corpora(stopwords_set,job_data)


In [10]:
for _, bow in corpora:
    print(_,bow)

Tokens for URL https://www.careerlink.vn/tim-viec/lai-chau-chuyen-vien-kinh-doanh/2729747?source=site: ['lai_châu']
https://www.careerlink.vn/tim-viec/lai-chau-chuyen-vien-kinh-doanh/2729747?source=site Counter({'lai_châu': 1})
Tokens for URL https://www.careerlink.vn/tim-viec-lam/lai-chau-chuyen-vien-kinh-doanh/2729747?source=site: ['lai_châu', 'chuyên_viên', 'kinh_doanh']
https://www.careerlink.vn/tim-viec-lam/lai-chau-chuyen-vien-kinh-doanh/2729747?source=site Counter({'lai_châu': 1, 'chuyên_viên': 1, 'kinh_doanh': 1})
Tokens for URL https://www.careerlink.vn/tim-viec-lam/quan-ly-cua-hang-nhan-hang-thoi-trang-calvin-klein-binh-tan/2729902?source=site: ['quản_lý', 'cửa_hàng', 'nhãn', 'hàng', 'thời_trang', 'calvin', 'klein', 'bình_tân']
https://www.careerlink.vn/tim-viec-lam/quan-ly-cua-hang-nhan-hang-thoi-trang-calvin-klein-binh-tan/2729902?source=site Counter({'quản_lý': 1, 'cửa_hàng': 1, 'nhãn': 1, 'hàng': 1, 'thời_trang': 1, 'calvin': 1, 'klein': 1, 'bình_tân': 1})
Tokens for URL 

In [13]:
for url, bow in corpora:
    print(url,bow)

Tokens for URL https://www.careerlink.vn/tim-viec/lai-chau-chuyen-vien-kinh-doanh/2729747?source=site: ['lai_châu']
https://www.careerlink.vn/tim-viec/lai-chau-chuyen-vien-kinh-doanh/2729747?source=site Counter({'lai_châu': 1})
Tokens for URL https://www.careerlink.vn/tim-viec-lam/lai-chau-chuyen-vien-kinh-doanh/2729747?source=site: ['lai_châu', 'chuyên_viên', 'kinh_doanh']
https://www.careerlink.vn/tim-viec-lam/lai-chau-chuyen-vien-kinh-doanh/2729747?source=site Counter({'lai_châu': 1, 'chuyên_viên': 1, 'kinh_doanh': 1})
Tokens for URL https://www.careerlink.vn/tim-viec-lam/quan-ly-cua-hang-nhan-hang-thoi-trang-calvin-klein-binh-tan/2729902?source=site: ['quản_lý', 'cửa_hàng', 'nhãn', 'hàng', 'thời_trang', 'calvin', 'klein', 'bình_tân']
https://www.careerlink.vn/tim-viec-lam/quan-ly-cua-hang-nhan-hang-thoi-trang-calvin-klein-binh-tan/2729902?source=site Counter({'quản_lý': 1, 'cửa_hàng': 1, 'nhãn': 1, 'hàng': 1, 'thời_trang': 1, 'calvin': 1, 'klein': 1, 'bình_tân': 1})
Tokens for URL 

**Đọc dữ liệu index và url**

In [18]:
with open("db/index.json", 'rb') as file:
    index_db = json.load(file)

with open("db/urls.json", 'rb') as file:
    urls = json.load(file)



**Tính df**

In [21]:

for url, bow in corpora:
    if url not in urls:
        urls.append(url)
        index = len(urls) - 1
        for term, freq in bow.items():
            if term not in index_db:
                index_db[term] = {'df': 0, 'postings_list': {}}
            index_db[term]['df'] += 1
            index_db[term]['postings_list'][index] = freq

Tokens for URL https://www.careerlink.vn/tim-viec-lam/quan-ly-cua-hang-nhan-hang-thoi-trang-calvin-klein-binh-tan/2729902?source=site: ['quản_lý', 'cửa_hàng', 'nhãn', 'hàng', 'thời_trang', 'calvin', 'klein', 'bình_tân']
Tokens for URL https://www.careerlink.vn/tim-viec-lam/vietinbank-quan-thu-duc-chuyen-vien-tu-van-vien-bao-hiem-kenh-hop-tac-ngan-hang/2745151?source=site: ['vietinbank', 'quận', 'thủ_đức', 'chuyên_viên', 'tư_vấn_viên', 'bảo_hiểm', 'kênh', 'hợp_tác', 'ngân_hàng']
Tokens for URL https://www.careerlink.vn/tim-viec-lam/outside-sales-staff-packing-material-ha%CC%80-nam/2725983?source=site: ['outside', 'sales', 'staff', 'packing', 'material', 'ha', 'nam']
Tokens for URL https://www.careerlink.vn/tim-viec-lam/cn-ha-noi-chuyen-vien-kinh-doanh-thu-nhap-len-den-30tr-thang/2729249?source=site: ['cn', 'hà_nội', 'chuyên_viên', 'kinh_doanh', 'thu_nhập', 'đến', 'tr', 'tháng']
Tokens for URL https://www.careerlink.vn/tim-viec-lam/h.me-linh-chuyen-vien-tu-van-bao-hiem-metlife-kenh-lien-

In [22]:
index_db

{'lai_châu': {'df': 5,
  'postings_list': {'0': 1, '1': 1, '1965': 1, '5850': 1, '5851': 1}},
 'chuyên_viên': {'df': 1613,
  'postings_list': {'1': 1,
   '3': 1,
   '5': 1,
   '6': 1,
   '7': 1,
   '8': 1,
   '11': 1,
   '15': 1,
   '16': 1,
   '28': 1,
   '31': 1,
   '64': 1,
   '67': 1,
   '69': 1,
   '70': 1,
   '71': 1,
   '72': 1,
   '73': 1,
   '83': 1,
   '85': 1,
   '88': 1,
   '90': 1,
   '92': 1,
   '93': 1,
   '94': 1,
   '96': 1,
   '98': 1,
   '106': 1,
   '109': 1,
   '110': 1,
   '112': 1,
   '114': 1,
   '128': 1,
   '149': 1,
   '151': 1,
   '153': 1,
   '155': 1,
   '157': 1,
   '169': 1,
   '170': 1,
   '173': 1,
   '180': 1,
   '182': 1,
   '190': 1,
   '193': 1,
   '194': 1,
   '196': 1,
   '198': 1,
   '200': 1,
   '202': 1,
   '208': 1,
   '211': 1,
   '212': 1,
   '215': 1,
   '216': 1,
   '217': 1,
   '218': 1,
   '219': 1,
   '220': 1,
   '221': 1,
   '223': 1,
   '224': 1,
   '225': 1,
   '226': 1,
   '227': 1,
   '228': 1,
   '230': 1,
   '231': 1,
   '232':

**Lưu lại index và url**

In [76]:
index_path = os.path.join(os.getcwd(), 'db', 'index.json')
with open(index_path, 'w',encoding='utf-8') as json_file:
    json.dump(index_db, json_file,ensure_ascii=False)

print(f'Index saved to {index_path}')

urls_path=os.path.join(os.getcwd(), 'db', 'urls.json')
with open(urls_path, 'w') as json_file:
    json.dump(urls, json_file)

print(f'Index saved to {urls_path}')

Index saved to c:\Users\Mai Vu Duy\Desktop\2023-1\pj3\Job_search\db\index.json
Index saved to c:\Users\Mai Vu Duy\Desktop\2023-1\pj3\Job_search\db\urls.json


In [78]:
with open("db/index.json", 'rb') as file:
    index_db = json.load(file)

with open("db/urls.json", 'rb') as file:
    urls = json.load(file)

**Tính độ dài của từng document**

In [80]:

num_docs = len(urls)
lengths = [0 for i in range(num_docs)]
for index in range(num_docs):
    # Re-construct doc vector from inverted index
    vector = []
    for term, value in index_db.items():
        df = value['df']
        postings_list = value['postings_list']
        str_index = str(index)
        if str_index in postings_list.keys():
            weight = helper.tf(postings_list[str_index]) * helper.idf(df, num_docs)
            vector.append(weight)

    lengths[index] = math.sqrt(sum((e ** 2 for e in vector)))


In [81]:
lengths

[7.227081356768379,
 7.644693986739235,
 15.401440338885275,
 9.6409072370293,
 16.236482070387698,
 10.801340377722688,
 13.050459736183974,
 11.120357304668309,
 13.60192001588454,
 6.073159655954687,
 12.299249236679078,
 11.693148784528708,
 8.023881390076584,
 15.86902325710593,
 10.001773177119441,
 9.889813619082327,
 10.595921698697897,
 16.068272385701455,
 16.58347056849082,
 22.36051171124752,
 16.78096992459776,
 18.015680284745304,
 6.931618822256752,
 22.86900007745477,
 14.373143315838954,
 10.798300795966686,
 11.017703076962073,
 7.7217234361441225,
 6.911044611083478,
 12.840951966902244,
 12.805458719461312,
 6.739205968134995,
 8.541095060043057,
 11.092317498214957,
 5.130257994796684,
 9.323220499080174,
 16.78840041165356,
 13.560490424024135,
 7.229668508677082,
 11.810800679979856,
 11.59699598981411,
 17.097958624301327,
 9.301662368496013,
 21.230736243538534,
 21.509712876414593,
 13.785658787003495,
 13.047200337742536,
 8.882538037332475,
 20.8523974216377

In [82]:
lengths_path=os.path.join(os.getcwd(), 'db', 'lengths.json')

with open(lengths_path, 'w') as json_file:
    json.dump(lengths, json_file)

print(f'Index saved to {lengths_path}')

Index saved to c:\Users\Mai Vu Duy\Desktop\2023-1\pj3\Job_search\db\lengths.json
